In [1]:
%matplotlib inline
%load_ext autoreload
%autoreload 2

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from IPython.display import Markdown, display, HTML
from collections import defaultdict

import torch
import torch.nn as nn
import torch.optim as optim
from livelossplot import PlotLosses

# Fix the dying kernel problem (only a problem in some installations - you can remove it, if it works without it)
import os
os.environ['KMP_DUPLICATE_LIB_OK'] = 'True'

# Load the dataset for recommenders

In [2]:
data_path = os.path.join("data", "hotel_data")

interactions_df = pd.read_csv(os.path.join(data_path, "hotel_data_interactions_df.csv"), index_col=0)

base_item_features = ['term', 'length_of_stay_bucket', 'rate_plan', 'room_segment', 'n_people_bucket', 'weekend_stay']

column_values_dict = {
    'term': ['WinterVacation', 'Easter', 'OffSeason', 'HighSeason', 'LowSeason', 'MayLongWeekend', 'NewYear', 'Christmas'],
    'length_of_stay_bucket': ['[0-1]', '[2-3]', '[4-7]', '[8-inf]'],
    'rate_plan': ['Standard', 'Nonref'],
    'room_segment': ['[0-160]', '[160-260]', '[260-360]', '[360-500]', '[500-900]'],
    'n_people_bucket': ['[1-1]', '[2-2]', '[3-4]', '[5-inf]'],
    'weekend_stay': ['True', 'False']
}

interactions_df.loc[:, 'term'] = pd.Categorical(
    interactions_df['term'], categories=column_values_dict['term'])
interactions_df.loc[:, 'length_of_stay_bucket'] = pd.Categorical(
    interactions_df['length_of_stay_bucket'], categories=column_values_dict['length_of_stay_bucket'])
interactions_df.loc[:, 'rate_plan'] = pd.Categorical(
    interactions_df['rate_plan'], categories=column_values_dict['rate_plan'])
interactions_df.loc[:, 'room_segment'] = pd.Categorical(
    interactions_df['room_segment'], categories=column_values_dict['room_segment'])
interactions_df.loc[:, 'n_people_bucket'] = pd.Categorical(
    interactions_df['n_people_bucket'], categories=column_values_dict['n_people_bucket'])
interactions_df.loc[:, 'weekend_stay'] = interactions_df['weekend_stay'].astype('str')
interactions_df.loc[:, 'weekend_stay'] = pd.Categorical(
    interactions_df['weekend_stay'], categories=column_values_dict['weekend_stay'])

display(HTML(interactions_df.head(15).to_html()))

In [15]:
from sklearn.preprocessing import OneHotEncoder
from sklearn.decomposition import PCA

def prepare_users_df(interactions_df):

    # Write your code here
    interactions_categories = interactions_df.loc[:,['term','length_of_stay_bucket','rate_plan','room_segment','n_people_bucket','weekend_stay']]
    ohe = OneHotEncoder(handle_unknown='ignore')
    ohe.fit(interactions_categories)
    
    interactions_user_categories = interactions_df.loc[:,['user_id','term','length_of_stay_bucket','rate_plan','room_segment','n_people_bucket','weekend_stay']]

    user_occurences = interactions_user_categories.groupby("user_id").count().sort_values(by="user_id")

    

    all_cols = list(interactions_user_categories.columns)
    all_cols.remove("user_id")

    main_users_df = pd.DataFrame()
    for i,elem in enumerate(all_cols):
        tmp_interactions_categories = interactions_user_categories.loc[:,["user_id",elem]]
        tmp_interactions_categories.loc[:,"ones"]=1
        tmp_pivot = pd.pivot_table(tmp_interactions_categories,index="user_id",columns=elem,values="ones",aggfunc=np.sum,fill_value=-1)

        tmp_pivot.columns=["uf"+str(i)+str(k) for k in range(len(column_values_dict.get(elem)))]

        if i==0:
            main_users_df=tmp_pivot
        else:
            main_users_df=pd.merge(main_users_df,tmp_pivot,on=["user_id"],how='left')
        
    main_users_df = main_users_df.apply(lambda x:(x/user_occurences['term']))
    main_users_df=main_users_df.fillna(-1.0)
    main_users_df[main_users_df<0.5]=0
    main_users_df[main_users_df==0.0]=-1
    
#     main_users_df = main_users_df.apply(lambda x:np.sin(x))
    
    
#     display(HTML(main_users_df.head(20).to_html()))
        
    users_df = main_users_df.reset_index().sort_values(by="user_id",ascending=True)
#     display(HTML(users_df.head(20).to_html()))

    user_features = list(users_df.columns)
    user_features.remove("user_id")
    
    return users_df, user_features
    

users_df, user_features = prepare_users_df(interactions_df)
# display(HTML(interactions_df.head(20).to_html()))

# print(user_features)
# display(HTML(users_df[users_df==np.NAN].head(20).to_html()))
display(HTML(users_df.loc[users_df['user_id'].isin([706, 1736, 7779, 96, 1, 50, 115])].head(30).to_html()))

In [10]:
from sklearn.preprocessing import OneHotEncoder
from sklearn.decomposition import PCA
def prepare_items_df(interactions_df):
    cols = ['item_id','term','length_of_stay_bucket','rate_plan','room_segment','n_people_bucket','weekend_stay']
    cats = []
    if 'if11' not in cols:
        cats = ['term','length_of_stay_bucket','rate_plan','room_segment','n_people_bucket','weekend_stay']
   
        interactions_item_categories = interactions_df.loc[:,cols]

        item_occurences = interactions_item_categories.groupby("item_id").count().sort_values(by="item_id")

        all_cols = list(interactions_item_categories.columns)
        all_cols.remove("item_id")

        main_items_df = pd.DataFrame()
        for i,elem in enumerate(all_cols):
            tmp_interactions_categories = interactions_item_categories.loc[:,["item_id",elem]]

            tmp_interactions_categories.loc[:,"ones"]=1
            tmp_pivot = pd.pivot_table(tmp_interactions_categories,index="item_id",columns=elem,values="ones",aggfunc=lambda x:1,fill_value=-1)            
            if len(tmp_pivot.columns)!=len(column_values_dict.get(elem)):
                diff = set(column_values_dict.get(elem))-set(tmp_pivot.columns)
                for ii in list(diff):
                    tmp_pivot.loc[:,ii]=-1

            tmp_pivot.columns=["if"+str(i)+str(k) for k in range(len(column_values_dict.get(elem)))]

            if i==0:
                main_items_df=tmp_pivot
            else:
                main_items_df=pd.merge(main_items_df,tmp_pivot,on=["item_id"],how='left')

        items_df = main_items_df.reset_index().sort_values(by="item_id",ascending=True)

    else:
        items_df = interactions_df
    items_df = items_df.fillna(-1)
    
    item_features = list(items_df.columns)
    item_features.remove("item_id")
    
    return items_df.loc[:,["item_id"]+item_features], item_features


items_df, item_features = prepare_items_df(interactions_df)

display(HTML(items_df.loc[items_df['item_id'].isin([0, 1, 2, 3, 4, 5, 6])].head(15).to_html()))

# (Optional) Prepare numerical user features

The method below is left here for convenience if you want to experiment with content-based user features as an input for your neural network.

In [30]:
def n_to_p(l):
    n = sum(l)
    return [x / n for x in l] if n > 0 else l

def calculate_p(x, values):
    counts = [0]*len(values)
    for v in x:
        counts[values.index(v)] += 1

    return n_to_p(counts)

def prepare_users_df(interactions_df):

    users_df = interactions_df.loc[:, ["user_id"]]
    users_df = users_df.groupby("user_id").first().reset_index(drop=False)
    
    user_features = []

    for column in base_item_features:

        column_values = column_values_dict[column]
        df = interactions_df.loc[:, ['user_id', column]]
        df = df.groupby('user_id').aggregate(lambda x: list(x)).reset_index(drop=False)

        def calc_p(x):
            return calculate_p(x, column_values)

        df.loc[:, column] = df[column].apply(lambda x: calc_p(x))

        p_columns = []
        for i in range(len(column_values)):
            p_columns.append("user_" + column + "_" + column_values[i])
            df.loc[:, p_columns[i]] = df[column].apply(lambda x: x[i])
            user_features.append(p_columns[i])

        users_df = pd.merge(users_df, df.loc[:, ['user_id'] + p_columns], on=["user_id"])
    
    return users_df, user_features
    

users_df, user_features = prepare_users_df(interactions_df)

print(user_features)

display(HTML(users_df.loc[users_df['user_id'].isin([706, 1736, 7779, 96, 1, 50, 115])].head(15).to_html()))

ValueError: nan is not in list

# (Optional) Prepare numerical item features

The method below is left here for convenience if you want to experiment with content-based item features as an input for your neural network.

In [ ]:
def map_items_to_onehot(df):
    one_hot = pd.get_dummies(df.loc[:, base_item_features])
    df = df.drop(base_item_features, axis = 1)
    df = df.join(one_hot)
    
    return df, list(one_hot.columns)

def prepare_items_df(interactions_df):
    items_df = interactions_df.loc[:, ["item_id"] + base_item_features].drop_duplicates()
    
    items_df, item_features = map_items_to_onehot(items_df)
    
    return items_df, item_features


items_df, item_features = prepare_items_df(interactions_df)

print(item_features)

display(HTML(items_df.loc[items_df['item_id'].isin([0, 1, 2, 3, 4, 5, 6])].head(15).to_html()))

# Neural network recommender

<span style="color:red"><font size="4">**Task:**</font></span><br> 
Code a recommender based on a neural network model. You are free to choose any network architecture you find appropriate. The network can use the interaction vectors for users and items, embeddings of users and items, as well as user and item features (you can use the features you developed in the first project).

Remember to keep control over randomness - in the init method add the seed as a parameter and initialize the random seed generator with that seed (both for numpy and pytorch):

```python
self.seed = seed
self.rng = np.random.RandomState(seed=seed)
```
in the network model:
```python
self.seed = torch.manual_seed(seed)
```

You are encouraged to experiment with:
  - the number of layers in the network, the number of neurons and different activation functions,
  - different optimizers and their parameters,
  - batch size and the number of epochs,
  - embedding layers,
  - content-based features of both users and items.

In [16]:
from recommenders.recommender import Recommender
from sklearn.preprocessing import StandardScaler, MinMaxScaler, Normalizer

from recommenders.recommender import Recommender
from sklearn.feature_selection import SelectKBest, chi2, f_regression,f_classif
from sklearn.decomposition import PCA
import math

class MyNetwork(nn.Module):
#     def __init__(self, n_items, n_users, embedding_dim, seed):
    def __init__(self, n_elems, embedding_dim, seed):
        super().__init__()
        self.seed = torch.manual_seed(seed)
        
#         self.u_colls = u_colls
#         self.i_colls = i_colls
#         self.elem_embedding = nn.Embedding(n_elems,embedding_dim)
#         self.user_embedding = nn.Embeding(n_users,embedding_dim)
        self.norm = nn.BatchNorm1d(26,affine=False)
        self.cos = nn.CosineSimilarity()
        self.fc1 = nn.Linear(n_elems, 64, bias=True)
        self.fc2 = nn.Linear(64, 64, bias=True)
        self.fc3 = nn.Linear(64, 64, bias=True)
#         self.fc3 = nn.Linear(128, 128, bias=False)
#         self.fc4 = nn.Linear(32, 32, bias=True)
#         self.fc5 = nn.Linear(8, 4, bias=False)
        self.fc6 = nn.Linear(64, 1, bias=True)
        
    
    def forward(self, x):
        vec1 = x[0,:,:]
        vec2 = x[1,:,:]
        
#         print("VEC1 ",vec1.shape)
#         print("VEC2 ",vec2.shape)
#         print("X shape ",x.shape)
#         elem_embedding = self.elem_embedding(x)
#         print("elem_embedding shape ",elem_embedding.shape)
#         item_embedding = self.item_embedding(item)1
#         x = torch.cat([user_embedding, item_embedding], dim=1)
#         vec1_norm = self.norm(vec1)
#         print("NORM1 ",vec1_norm)
#         vec2_norm = self.norm(vec2)
        vec3 = vec1*vec2
#         dot = torch.unsqueeze(vec3.sum(),1)
        dot = torch.unsqueeze(torch.sum(vec3,dim=1),1)
#         print(dot.shape)
        sim = torch.unsqueeze(self.cos(vec1,vec2),1)
#         print(sim.shape)
#         vec3 = self.norm(vec3)
        x = torch.cat([vec3,sim],dim=1)
        x = self.norm(x)
        x = torch.sigmoid(self.fc1(x))
        x = torch.relu(self.fc2(x))
        x = torch.sigmoid(self.fc3(x))
#         x = torch.relu(self.fc4(x))

#         x = torch.relu(self.fc5(x))
        x = torch.sigmoid(self.fc6(x))
        
        return x

class NNRecommender(Recommender):
    """
    Linear recommender class based on user and item features.
    """
    
    def __init__(self, seed=6789, n_neg_per_pos=5):
        """
        Initialize base recommender params and variables.
        """
        self.model = None
        self.n_neg_per_pos = n_neg_per_pos
        
        self.recommender_df = pd.DataFrame(columns=['user_id', 'item_id', 'score'])
        self.users_df = None
        self.user_features = None
        
        self.seed = seed
        self.rng = np.random.RandomState(seed=seed)
        self.network = None
        self.final_std = None
        self.final_norm = None
        self.model_features = None
        self.importance = None
        
    def get_best_features(self,interactions_df,prod_features,k):
        selector = SelectKBest(f_regression, k=k)
        prod_features_df = interactions_df.loc[:,prod_features+["interacted"]]
        y = prod_features_df['interacted'].values

        X = prod_features_df.loc[:,prod_features].values

        selector.fit(X, y)
        
        cols = selector.get_support(indices=True)
        features_with_scores = sorted([("prod"+str(index),elem) for index,elem in enumerate(selector.scores_) if not math.isnan(elem)],key=lambda x:x[1],reverse=True)[:k]
        features_with_scores = {i:v for i,v in features_with_scores}
        total = sum(features_with_scores.values())
        self.importance = {k:float(v/total) for k,v in features_with_scores.items()}

        selected_features_df = prod_features_df.iloc[:,cols]
        selected_features = selected_features_df.columns.tolist()

        features_df_new = interactions_df.loc[:,selected_features+["interacted"]]

        self.model_features = selected_features
        return features_df_new
    
    def fit(self, interactions_df, users_df, items_df):
        """
        Training of the recommender.
        
        :param pd.DataFrame interactions_df: DataFrame with recorded interactions between users and items 
            defined by user_id, item_id and features of the interaction.
        :param pd.DataFrame users_df: DataFrame with users and their features defined by user_id and the user feature columns.
        :param pd.DataFrame items_df: DataFrame with items and their features defined by item_id and the item feature columns.
        """
        
        interactions_df = interactions_df.copy()
        interactions_df.loc[:,"interacted"] = 1
        
        # Prepare users_df and items_df 
        # (optional - use only if you want to train a hybrid model with content-based features)
        
        users_df, user_features = prepare_users_df(interactions_df)
        
        self.users_df = users_df
        self.user_features = user_features
        
        items_df, item_features = prepare_items_df(interactions_df)
        items_df = items_df.loc[:, ['item_id'] + item_features]
        
        # Generate negative interactions
        
        # <<<Write your code here>>>
        negative_interactions = []
        
        items_unique = interactions_df.loc[:,"item_id"].unique()
        users_unique = interactions_df.loc[:,"user_id"].unique()

        desire=int(self.n_neg_per_pos * len(interactions_df))
        hmany=100
        rng = np.random.RandomState(seed=6789)
        real_interaction = interactions_df.loc[:,["user_id","item_id"]]
        length = 0
        total_negative_interactions=pd.DataFrame(negative_interactions)
        while length!=desire and length<desire :
            it = rng.choice(items_unique,hmany)
            us = rng.choice(users_unique,hmany)
            tmp_negative_interaction = pd.DataFrame({'user_id':us,'item_id':it}).drop_duplicates()

            result = pd.merge(tmp_negative_interaction,real_interaction,on=["user_id","item_id"])
            if len(result)==0:
                total_negative_interactions = pd.concat([total_negative_interactions,tmp_negative_interaction]).drop_duplicates()
                length = total_negative_interactions.size

        total_negative_interactions = total_negative_interactions.iloc[:desire]
        total_negative_interactions.loc[:,'interacted']=0
        negative_interactions = total_negative_interactions.to_numpy()
#         print("neg iter")
#         display(HTML(total_negative_interactions.head(10).to_html()))
        
        
        interactions_df = pd.concat(
            [interactions_df, pd.DataFrame(negative_interactions, columns=['user_id', 'item_id', 'interacted'])])
        
        # Merge user and item features
        # (optional - use only if you want to train a hybrid model with content-based features)
        
        interactions_df = pd.merge(interactions_df, users_df, on=['user_id'])
        interactions_df = pd.merge(interactions_df, items_df, on=['item_id'])
        
#         print("Shape ",interactions_df.shape[0])
        
        
        interactions_df = interactions_df.drop_duplicates()
#         display(HTML(interactions_df.loc[:,['user_id', 'item_id', 'interacted']].head(20).to_html()))
        
#         print("Shape 2 ",interactions_df.shape[0])
        
        u_colls = users_df.columns.tolist()
        u_colls.remove("user_id")
        i_colls = items_df.columns.tolist()
        i_colls.remove("item_id")
        
        


#         prod_cols=[]
#             new
        prod_cols = u_colls + i_colls

#         for index,elem in enumerate(zip(u_colls,i_colls)):

#             tmp_result = interactions_df.loc[:,elem[0]] * interactions_df.loc[:,elem[1]]
# #             print("COLS: ", interactions_df.loc[:,elem[0]]," :: ",interactions_df.loc[:,elem[1]])
# #             tmp_result = interactions_df.loc[:,elem[0]] + interactions_df.loc[:,elem[1]]
#             interactions_df.loc[:,"prod"+str(index)]=tmp_result
#             prod_cols.append("prod"+str(index))
            
#         print("PROD COLS ",u_colls)


    
        new_interactions_df = interactions_df
#         display(HTML(new_interactions_df.head(10).to_html()))
        
        self.model_features = prod_cols
#         print(len(self.model_features))


        
#         self.final_norm = Normalizer()
#         scaled_df = pd.DataFrame(self.final_norm.fit_transform(new_interactions_df.loc[:,self.model_features]),columns=self.model_features)
#         self.final_std = StandardScaler()
#         scaled_df = pd.DataFrame(self.final_std.fit_transform(scaled_df.loc[:,self.model_features]),columns=self.model_features)
#         sec_norm = Normalizer()
#         scaled_df = pd.DataFrame(sec_norm.fit_transform(scaled_df.loc[:,self.model_features]),columns=self.model_features)
#         scaled_df = new_interactions_df.loc[:,self.model_features]
#         scaled_df.replace([np.inf, -np.inf], np.nan,inplace=True)
#         scaled_df = scaled_df.fillna(0)
#         print(np.min(scaled_df))
        

        
#         print(scaled_df.isinf())
#         display(HTML(scaled_df.head(10).to_html()))
#         scaled_df.loc[:,'interacted'] = new_interactions_df['interacted']
#         scaled_df = scaled_df.round(2)
#         scaled_df.astype('float64')
#         display(HTML(scaled_df.head(10).to_html()))

#         scaled_df = self.get_best_features(scaled_df,prod_cols,k=11)


        
        
        x = new_interactions_df.loc[:,self.model_features]
        y = new_interactions_df['interacted'].to_frame()
        
#         pca = PCA(10)
#         pcaed = pca.fit_transform(x,y)
#         print("X: ",x.dtype)
#         display(HTML(pcaed)))
        
        interaction_ids = self.rng.permutation(len(x))
        limit_id = int(0.1*len(interaction_ids))
        validation_ids = interaction_ids[:limit_id]
        
        train_ids = interaction_ids[limit_id:]
        
#         print(len(validation_ids))
        
#         display(HTML(x.iloc[validation_ids].head(10).to_html()))
#         print(torch.from_numpy(x.iloc[train_ids].to_numpy()))
#         x_train = []
#         for index,data in x.iloc[train_ids].iterrows():
#             tmp_df = data.to_frame().transpose()
# #             display(HTML(tmp_df.to_html()))
#             x1 = torch.tensor(tmp_df.loc[:,u_colls].to_numpy()).float()
#             x2 = torch.tensor(tmp_df.loc[:,i_colls].to_numpy()).float()
#             x_train.append([x1,x2])
#         x_train = torch.stack(x_train,dim=0)
#         print("x_Train ",x_train)
#         x_train = torch.tensor(x.iloc[train_ids].to_numpy()).float()
        x_train = torch.tensor([(x.iloc[train_ids].loc[:,u_colls].to_numpy()),(x.iloc[train_ids].loc[:,i_colls].to_numpy())]).float()
        y_train = torch.tensor(y.iloc[train_ids].to_numpy()).float()
        x_val= torch.tensor([(x.iloc[validation_ids].loc[:,u_colls].to_numpy()),(x.iloc[validation_ids].loc[:,i_colls].to_numpy())]).float()
#         torch.tensor(x.iloc[validation_ids].to_numpy()).float()
        y_val = torch.tensor(y.iloc[validation_ids].to_numpy()).float()
        
#         x_train = torch.tensor(x.to_numpy()).float()
#         y_train = torch.tensor(y.to_numpy()).float()
        
#         print(x_val.shape[0])

        # Initialize the neural network model
        print(x_train.shape[1])
        
#         # <<<Write your code here>>>
        self.network = MyNetwork(26,16,6789)
        
#         self.optimizer = optim.Adam(self.network.parameters(),lr = 0.0001)
#         self.optimizer = optim.SGD(self.network.parameters(),lr = 0.000173)     
#         self.optimizer = optim.SGD(self.network.parameters(),lr = 0.0001) 
        self.optimizer = optim.Adadelta(self.network.parameters(),lr=0.01) 
        
        # Train the model using an optimizer
#         epochs = 2000
#         epochs = 200
#         batch_size = 4100
        epochs = 7000
        batch_size = int((x_train.shape[1]/10)+1)
        n_batches = int(np.ceil((x_train.shape[1])/batch_size))
        for epoch in range(epochs):
            for batch in range(n_batches):
                x_tmp = x_train[:,(batch*batch_size):((batch+1)*batch_size),:]
                y_tmp = y_train[(batch*batch_size):((batch+1)*batch_size) ]
                self.network.train()
                self.optimizer.zero_grad()
#                 print(x_tmp.dtype)
                y_hat_train = self.network(x_tmp).clip(0.000001, 0.999999)
#                 y_hat_train = y_hat_train[:,:]
#                 print(y_hat_train)
                loss = - ((y_tmp * y_hat_train.log()) + ((1 - y_tmp) * (1-y_hat_train).log())).sum()
                loss.backward()
                self.optimizer.step()

                self.network.eval()
                with torch.no_grad():
                    y_hat_val = self.network(x_val).clip(0.000001, 0.999999)
                    print("RESULTS: ",torch.cat([y_val,y_hat_val,(y_val-y_hat_val).abs()],dim=1))
                    print("MAX: ",torch.where((y_val-y_hat_val).abs()>0.5,0.0,1.0).sum())
                    loss_val = - ((y_val * y_hat_val.log()) + ((1 - y_val) * (1-y_hat_val).log()) ).sum()
                    print(epoch," :: ",loss_val)
#                     print("y diff ",torch.cat([y_val,y_hat_val],axis=1))
                
            
        
        # <<<Write your code here>>>
    
    def recommend(self, users_df, items_df, n_recommendations=1):
        """
        Serving of recommendations. Scores items in items_df for each user in users_df and returns 
        top n_recommendations for each user.
        
        :param pd.DataFrame users_df: DataFrame with users and their features for which recommendations should be generated.
        :param pd.DataFrame items_df: DataFrame with items and their features which should be scored.
        :param int n_recommendations: Number of recommendations to be returned for each user.
        :return: DataFrame with user_id, item_id and score as columns returning n_recommendations top recommendations 
            for each user.
        :rtype: pd.DataFrame
        """
        
        # Clean previous recommendations (iloc could be used alternatively)
        self.recommender_df = self.recommender_df[:0]
        
        # Prepare users_df and items_df
        # (optional - use only if you want to train a hybrid model with content-based features)
        
        users_df = users_df.loc[:, 'user_id']
        users_df = pd.merge(users_df, self.users_df, on=['user_id'], how='left').fillna(0)
#         display(HTML(users_df.head(10).to_html()))
        
        items_df, item_features = prepare_items_df(items_df)
        items_df = items_df.loc[:, ['item_id'] + item_features]
        
        
        
        # Score the items
    
        recommendations = pd.DataFrame(columns=['user_id', 'item_id', 'score'])
#         print("users")
#         display(HTML(users_df.head(10).to_html()))
        for ix, user in users_df.iterrows():
            
            # Calculate the score for the user and every item in items_df
            interactions_df = pd.merge(user.to_frame().transpose(),items_df,how="cross")
            
#             print("interactions_df")
#             display(HTML(interactions_df.head(10).to_html()))
            
            u_colls = users_df.columns.tolist()
            u_colls.remove("user_id")
            i_colls = items_df.columns.tolist()
            i_colls.remove("item_id")


            prod_cols=[]

            for index,elem in enumerate(zip(u_colls,i_colls)):

                tmp_result = interactions_df.loc[:,elem[0]] * interactions_df.loc[:,elem[1]]
                interactions_df.loc[:,"prod"+str(index)]=tmp_result
                prod_cols.append("prod"+str(index))

            interactions_df = interactions_df.fillna(0)

            new_interactions_df = interactions_df.loc[:,self.model_features]
            
#             print("new_interactions_df")
#             display(HTML(new_interactions_df.head(10).to_html()))

            scaled_df = pd.DataFrame(self.final_norm.transform(new_interactions_df.loc[:,self.model_features]),columns=self.model_features)            
            scaled_df = pd.DataFrame(self.final_std.transform(scaled_df.loc[:,self.model_features]),columns=self.model_features)

            x = scaled_df.loc[:,self.model_features]
            x_test = torch.tensor(x.to_numpy()).float()
            self.network.eval()
            with torch.no_grad():
                out = self.network(x_test)
            print("out")
            display(HTML(out.head(20).to_html()))
            
            scores = out.squeeze().numpy()
#             print((scores))
#             scores = []
#             arr = np.array([0.49140155, 0.86761564, 0.22462055, 0.62140334, 0.01714047])
            chosen_ids = np.argsort(-scores)[:n_recommendations].tolist()
#             print("Chosen ",chosen_ids)
            scores = scores.squeeze().tolist()
#             print("Scores ",scores)
            
            recommendations = []
            for item_id in chosen_ids:
#                 print(item_id)
                recommendations.append(
                    {
                        'user_id': user['user_id'],
                        'item_id': item_id,
                        'score': scores[item_id]
                    }
                )
            user_recommendations = pd.DataFrame(recommendations)

            self.recommender_df = pd.concat([self.recommender_df, user_recommendations])

        return self.recommender_df

# Quick test of the recommender

In [17]:
items_df = interactions_df.loc[:, ['item_id'] + base_item_features].drop_duplicates()

In [ ]:
# Fit method
nn_recommender = NNRecommender()
nn_recommender.fit(interactions_df, None, None)

50357
RESULTS:  tensor([[0.0000, 0.4947, 0.4947],
        [0.0000, 0.4943, 0.4943],
        [0.0000, 0.4948, 0.4948],
        ...,
        [1.0000, 0.4943, 0.5057],
        [1.0000, 0.4949, 0.5051],
        [1.0000, 0.4951, 0.5049]])
MAX:  tensor(0.5064)
0  ::  tensor(3848.2664)
RESULTS:  tensor([[0.0000, 0.4943, 0.4943],
        [0.0000, 0.4939, 0.4939],
        [0.0000, 0.4944, 0.4944],
        ...,
        [1.0000, 0.4939, 0.5061],
        [1.0000, 0.4945, 0.5055],
        [1.0000, 0.4947, 0.5053]])
MAX:  tensor(0.5068)
0  ::  tensor(3846.2627)
RESULTS:  tensor([[0.0000, 0.4939, 0.4939],
        [0.0000, 0.4935, 0.4935],
        [0.0000, 0.4940, 0.4940],
        ...,
        [1.0000, 0.4935, 0.5065],
        [1.0000, 0.4941, 0.5059],
        [1.0000, 0.4943, 0.5057]])
MAX:  tensor(0.5073)
0  ::  tensor(3844.2595)
RESULTS:  tensor([[0.0000, 0.4935, 0.4935],
        [0.0000, 0.4931, 0.4931],
        [0.0000, 0.4937, 0.4937],
        ...,
        [1.0000, 0.4931, 0.5069],
        [1.00

RESULTS:  tensor([[0.0000, 0.4668, 0.4668],
        [0.0000, 0.4645, 0.4645],
        [0.0000, 0.4665, 0.4665],
        ...,
        [1.0000, 0.4654, 0.5346],
        [1.0000, 0.4672, 0.5328],
        [1.0000, 0.4668, 0.5332]])
MAX:  tensor(0.5375)
4  ::  tensor(3709.5264)
RESULTS:  tensor([[0.0000, 0.4641, 0.4641],
        [0.0000, 0.4618, 0.4618],
        [0.0000, 0.4636, 0.4636],
        ...,
        [1.0000, 0.4627, 0.5373],
        [1.0000, 0.4647, 0.5353],
        [1.0000, 0.4640, 0.5360]])
MAX:  tensor(0.5405)
4  ::  tensor(3696.8721)
RESULTS:  tensor([[0.0000, 0.4604, 0.4604],
        [0.0000, 0.4582, 0.4582],
        [0.0000, 0.4600, 0.4600],
        ...,
        [1.0000, 0.4592, 0.5408],
        [1.0000, 0.4613, 0.5387],
        [1.0000, 0.4605, 0.5395]])
MAX:  tensor(0.5443)
4  ::  tensor(3680.9841)
RESULTS:  tensor([[0.0000, 0.4562, 0.4562],
        [0.0000, 0.4540, 0.4540],
        [0.0000, 0.4559, 0.4559],
        ...,
        [1.0000, 0.4552, 0.5448],
        [1.0000, 0.

RESULTS:  tensor([[0.0000, 0.2644, 0.2644],
        [0.0000, 0.2884, 0.2884],
        [0.0000, 0.2344, 0.2344],
        ...,
        [1.0000, 0.4115, 0.5885],
        [1.0000, 0.4447, 0.5553],
        [1.0000, 0.4367, 0.5633]])
MAX:  tensor(0.7596)
9  ::  tensor(2627.6284)
RESULTS:  tensor([[0.0000, 0.2578, 0.2578],
        [0.0000, 0.2840, 0.2840],
        [0.0000, 0.2272, 0.2272],
        ...,
        [1.0000, 0.4190, 0.5810],
        [1.0000, 0.4550, 0.5450],
        [1.0000, 0.4464, 0.5536]])
MAX:  tensor(0.7660)
9  ::  tensor(2573.3240)
RESULTS:  tensor([[0.0000, 0.2556, 0.2556],
        [0.0000, 0.2846, 0.2846],
        [0.0000, 0.2234, 0.2234],
        ...,
        [1.0000, 0.4346, 0.5654],
        [1.0000, 0.4725, 0.5275],
        [1.0000, 0.4646, 0.5354]])
MAX:  tensor(0.7688)
9  ::  tensor(2514.7551)
RESULTS:  tensor([[0.0000, 0.2584, 0.2584],
        [0.0000, 0.2912, 0.2912],
        [0.0000, 0.2232, 0.2232],
        ...,
        [1.0000, 0.4602, 0.5398],
        [1.0000, 0.

RESULTS:  tensor([[0.0000, 0.1126, 0.1126],
        [0.0000, 0.1318, 0.1318],
        [0.0000, 0.1116, 0.1116],
        ...,
        [1.0000, 0.7992, 0.2008],
        [1.0000, 0.8202, 0.1798],
        [1.0000, 0.8195, 0.1805]])
MAX:  tensor(0.8866)
13  ::  tensor(1134.8804)
RESULTS:  tensor([[0.0000, 0.1118, 0.1118],
        [0.0000, 0.1286, 0.1286],
        [0.0000, 0.1109, 0.1109],
        ...,
        [1.0000, 0.7962, 0.2038],
        [1.0000, 0.8182, 0.1818],
        [1.0000, 0.8173, 0.1827]])
MAX:  tensor(0.8874)
13  ::  tensor(1126.7341)
RESULTS:  tensor([[0.0000, 0.1114, 0.1114],
        [0.0000, 0.1282, 0.1282],
        [0.0000, 0.1105, 0.1105],
        ...,
        [1.0000, 0.8022, 0.1978],
        [1.0000, 0.8225, 0.1775],
        [1.0000, 0.8218, 0.1782]])
MAX:  tensor(0.8879)
13  ::  tensor(1117.7181)
RESULTS:  tensor([[0.0000, 0.1111, 0.1111],
        [0.0000, 0.1289, 0.1289],
        [0.0000, 0.1102, 0.1102],
        ...,
        [1.0000, 0.8108, 0.1892],
        [1.0000,

RESULTS:  tensor([[0.0000, 0.0996, 0.0996],
        [0.0000, 0.1030, 0.1030],
        [0.0000, 0.0993, 0.0993],
        ...,
        [1.0000, 0.8537, 0.1463],
        [1.0000, 0.8612, 0.1388],
        [1.0000, 0.8606, 0.1394]])
MAX:  tensor(0.9002)
18  ::  tensor(945.3539)
RESULTS:  tensor([[0.0000, 0.0994, 0.0994],
        [0.0000, 0.1026, 0.1026],
        [0.0000, 0.0991, 0.0991],
        ...,
        [1.0000, 0.8523, 0.1477],
        [1.0000, 0.8602, 0.1398],
        [1.0000, 0.8593, 0.1407]])
MAX:  tensor(0.9004)
18  ::  tensor(944.0325)
RESULTS:  tensor([[0.0000, 0.0992, 0.0992],
        [0.0000, 0.1025, 0.1025],
        [0.0000, 0.0989, 0.0989],
        ...,
        [1.0000, 0.8546, 0.1454],
        [1.0000, 0.8619, 0.1381],
        [1.0000, 0.8611, 0.1389]])
MAX:  tensor(0.9006)
18  ::  tensor(941.7264)
RESULTS:  tensor([[0.0000, 0.0991, 0.0991],
        [0.0000, 0.1024, 0.1024],
        [0.0000, 0.0988, 0.0988],
        ...,
        [1.0000, 0.8558, 0.1442],
        [1.0000, 0.

...

RESULTS:  tensor([[0.0000e+00, 2.4898e-04, 2.4898e-04],
        [0.0000e+00, 5.0071e-04, 5.0071e-04],
        [0.0000e+00, 7.2097e-04, 7.2097e-04],
        ...,
        [1.0000e+00, 9.9724e-01, 2.7602e-03],
        [1.0000e+00, 9.9512e-01, 4.8783e-03],
        [1.0000e+00, 9.9886e-01, 1.1373e-03]])
MAX:  tensor(0.9993)
2362  ::  tensor(92.9505)
RESULTS:  tensor([[0.0000e+00, 2.6357e-04, 2.6357e-04],
        [0.0000e+00, 5.1011e-04, 5.1011e-04],
        [0.0000e+00, 7.3896e-04, 7.3896e-04],
        ...,
        [1.0000e+00, 9.9736e-01, 2.6354e-03],
        [1.0000e+00, 9.9553e-01, 4.4748e-03],
        [1.0000e+00, 9.9894e-01, 1.0630e-03]])
MAX:  tensor(0.9993)
2362  ::  tensor(92.8845)
RESULTS:  tensor([[0.0000e+00, 2.5566e-04, 2.5566e-04],
        [0.0000e+00, 5.1802e-04, 5.1802e-04],
        [0.0000e+00, 7.5656e-04, 7.5656e-04],
        ...,
        [1.0000e+00, 9.9740e-01, 2.6023e-03],
        [1.0000e+00, 9.9576e-01, 4.2397e-03],
        [1.0000e+00, 9.9897e-01, 1.0338e-03]])
MAX:  

MAX:  tensor(0.9993)
2366  ::  tensor(92.8783)
RESULTS:  tensor([[0.0000e+00, 2.4799e-04, 2.4799e-04],
        [0.0000e+00, 5.2944e-04, 5.2944e-04],
        [0.0000e+00, 7.5647e-04, 7.5647e-04],
        ...,
        [1.0000e+00, 9.9741e-01, 2.5862e-03],
        [1.0000e+00, 9.9572e-01, 4.2823e-03],
        [1.0000e+00, 9.9895e-01, 1.0482e-03]])
MAX:  tensor(0.9993)
2366  ::  tensor(92.9130)
RESULTS:  tensor([[0.0000e+00, 2.6090e-04, 2.6090e-04],
        [0.0000e+00, 5.3246e-04, 5.3246e-04],
        [0.0000e+00, 7.7366e-04, 7.7366e-04],
        ...,
        [1.0000e+00, 9.9759e-01, 2.4063e-03],
        [1.0000e+00, 9.9579e-01, 4.2082e-03],
        [1.0000e+00, 9.9900e-01, 9.9927e-04]])
MAX:  tensor(0.9993)
2366  ::  tensor(92.9389)
RESULTS:  tensor([[0.0000e+00, 2.4729e-04, 2.4729e-04],
        [0.0000e+00, 5.1096e-04, 5.1096e-04],
        [0.0000e+00, 7.4427e-04, 7.4427e-04],
        ...,
        [1.0000e+00, 9.9740e-01, 2.5972e-03],
        [1.0000e+00, 9.9552e-01, 4.4844e-03],
      

RESULTS:  tensor([[0.0000e+00, 2.4303e-04, 2.4303e-04],
        [0.0000e+00, 4.9040e-04, 4.9040e-04],
        [0.0000e+00, 7.1224e-04, 7.1224e-04],
        ...,
        [1.0000e+00, 9.9727e-01, 2.7335e-03],
        [1.0000e+00, 9.9516e-01, 4.8366e-03],
        [1.0000e+00, 9.9887e-01, 1.1275e-03]])
MAX:  tensor(0.9993)
2371  ::  tensor(92.6753)
RESULTS:  tensor([[0.0000e+00, 2.5737e-04, 2.5737e-04],
        [0.0000e+00, 4.9964e-04, 4.9964e-04],
        [0.0000e+00, 7.3010e-04, 7.3010e-04],
        ...,
        [1.0000e+00, 9.9739e-01, 2.6101e-03],
        [1.0000e+00, 9.9556e-01, 4.4369e-03],
        [1.0000e+00, 9.9895e-01, 1.0539e-03]])
MAX:  tensor(0.9993)
2371  ::  tensor(92.6102)
RESULTS:  tensor([[0.0000e+00, 2.4955e-04, 2.4955e-04],
        [0.0000e+00, 5.0730e-04, 5.0730e-04],
        [0.0000e+00, 7.4739e-04, 7.4739e-04],
        ...,
        [1.0000e+00, 9.9742e-01, 2.5802e-03],
        [1.0000e+00, 9.9580e-01, 4.2048e-03],
        [1.0000e+00, 9.9897e-01, 1.0258e-03]])
MAX:  

RESULTS:  tensor([[0.0000e+00, 2.3562e-04, 2.3562e-04],
        [0.0000e+00, 4.8995e-04, 4.8995e-04],
        [0.0000e+00, 7.1759e-04, 7.1759e-04],
        ...,
        [1.0000e+00, 9.9709e-01, 2.9100e-03],
        [1.0000e+00, 9.9541e-01, 4.5851e-03],
        [1.0000e+00, 9.9886e-01, 1.1419e-03]])
MAX:  tensor(0.9993)
2375  ::  tensor(92.7804)
RESULTS:  tensor([[0.0000e+00, 2.4965e-04, 2.4965e-04],
        [0.0000e+00, 5.1060e-04, 5.1060e-04],
        [0.0000e+00, 7.4246e-04, 7.4246e-04],
        ...,
        [1.0000e+00, 9.9734e-01, 2.6647e-03],
        [1.0000e+00, 9.9556e-01, 4.4386e-03],
        [1.0000e+00, 9.9889e-01, 1.1052e-03]])
MAX:  tensor(0.9993)
2375  ::  tensor(92.6047)
RESULTS:  tensor([[0.0000e+00, 2.4858e-04, 2.4858e-04],
        [0.0000e+00, 5.1989e-04, 5.1989e-04],
        [0.0000e+00, 7.3847e-04, 7.3847e-04],
        ...,
        [1.0000e+00, 9.9749e-01, 2.5084e-03],
        [1.0000e+00, 9.9571e-01, 4.2876e-03],
        [1.0000e+00, 9.9895e-01, 1.0545e-03]])
MAX:  

RESULTS:  tensor([[0.0000e+00, 2.5247e-04, 2.5247e-04],
        [0.0000e+00, 5.1797e-04, 5.1797e-04],
        [0.0000e+00, 7.6205e-04, 7.6205e-04],
        ...,
        [1.0000e+00, 9.9762e-01, 2.3765e-03],
        [1.0000e+00, 9.9583e-01, 4.1687e-03],
        [1.0000e+00, 9.9901e-01, 9.8884e-04]])
MAX:  tensor(0.9993)
2379  ::  tensor(92.5482)
RESULTS:  tensor([[0.0000e+00, 2.3921e-04, 2.3921e-04],
        [0.0000e+00, 4.9688e-04, 4.9688e-04],
        [0.0000e+00, 7.3285e-04, 7.3285e-04],
        ...,
        [1.0000e+00, 9.9744e-01, 2.5630e-03],
        [1.0000e+00, 9.9556e-01, 4.4391e-03],
        [1.0000e+00, 9.9895e-01, 1.0517e-03]])
MAX:  tensor(0.9993)
2380  ::  tensor(92.4214)
RESULTS:  tensor([[0.0000e+00, 2.3752e-04, 2.3752e-04],
        [0.0000e+00, 4.8162e-04, 4.8162e-04],
        [0.0000e+00, 7.0505e-04, 7.0505e-04],
        ...,
        [1.0000e+00, 9.9729e-01, 2.7099e-03],
        [1.0000e+00, 9.9520e-01, 4.8035e-03],
        [1.0000e+00, 9.9888e-01, 1.1188e-03]])
MAX:  

In [ ]:
## Recommender method

recommendations = nn_recommender.recommend(pd.DataFrame([[1], [2], [3], [4], [5]], columns=['user_id']), items_df, 10)

recommendations = pd.merge(recommendations, items_df, on='item_id', how='left')
display(HTML(recommendations.sort_values(by=["user_id","score"],ascending=True).to_html()))

# Tuning method

In [115]:
from evaluation_and_testing.testing import evaluate_train_test_split_implicit

seed = 6789

In [11]:
from hyperopt import hp, fmin, tpe, Trials
import traceback

def tune_recommender(recommender_class, interactions_df, items_df, 
                     param_space, max_evals=1, show_progressbar=True, seed=6789):
    # Split into train_validation and test sets

    shuffle = np.arange(len(interactions_df))
    rng = np.random.RandomState(seed=seed)
    rng.shuffle(shuffle)
    shuffle = list(shuffle)

    train_test_split = 0.8
    split_index = int(len(interactions_df) * train_test_split)

    train_validation = interactions_df.iloc[shuffle[:split_index]]
    test = interactions_df.iloc[shuffle[split_index:]]

    # Tune

    def loss(tuned_params):
        recommender = recommender_class(seed=seed, **tuned_params)
        hr1, hr3, hr5, hr10, ndcg1, ndcg3, ndcg5, ndcg10 = evaluate_train_test_split_implicit(
            recommender, train_validation, items_df, seed=seed)
        return -hr10

    n_tries = 1
    succeded = False
    try_id = 0
    while not succeded and try_id < n_tries:
        try:
            trials = Trials()
            best_param_set = fmin(loss, space=param_space, algo=tpe.suggest, 
                                  max_evals=max_evals, show_progressbar=show_progressbar, trials=trials, verbose=True)
            succeded = True
        except:
            traceback.print_exc()
            try_id += 1
            
    if not succeded:
        return None
        
    # Validate
    
    recommender = recommender_class(seed=seed, **best_param_set)

    results = [[recommender_class.__name__] + list(evaluate_train_test_split_implicit(
        recommender, {'train': train_validation, 'test': test}, items_df, seed=seed))]

    results = pd.DataFrame(results, 
                           columns=['Recommender', 'HR@1', 'HR@3', 'HR@5', 'HR@10', 'NDCG@1', 'NDCG@3', 'NDCG@5', 'NDCG@10'])

    display(HTML(results.to_html()))
    
    return best_param_set

## Tuning of the recommender

<span style="color:red"><font size="4">**Task:**</font></span><br> 
Tune your model using the code below. You only need to put the class name of your recommender and choose an appropriate parameter space.

In [230]:
param_space = {
    'n_neg_per_pos': hp.quniform('n_neg_per_pos', 1, 10, 1)
}

best_param_set = tune_recommender(NNRecommender, interactions_df, items_df,
                                  param_space, max_evals=10, show_progressbar=True, seed=seed)

print("Best parameters:")
print(best_param_set)

25                                                    
25                                                                                   
25                                                                                   
25                                                                                   
25                                                                                   
25                                                                                 
25                                                                                   
25                                                                                   
25                                                                                   
25                                                                                   
100%|██████████| 10/10 [1:44:22<00:00, 626.21s/trial, best loss: -0.04424416222859484]
25


Best parameters:
{'n_neg_per_pos': 2.0}


# Final evaluation

<span style="color:red"><font size="4">**Task:**</font></span><br> 
Run the final evaluation of your recommender and present its results against the Amazon and Netflix recommenders' results. You just need to give the class name of your recommender and its tuned parameters below.

In [116]:
nn_recommender = NNRecommender(n_neg_per_pos=2)  # Initialize your recommender here
# nn_recommender.fit(interactions_df, None, None)
# Give the name of your recommender in the line below
nn_tts_results = [['NNRecommender'] + list(evaluate_train_test_split_implicit(
    nn_recommender, interactions_df, items_df))]

nn_tts_results = pd.DataFrame(
    nn_tts_results, columns=['Recommender', 'HR@1', 'HR@3', 'HR@5', 'HR@10', 'NDCG@1', 'NDCG@3', 'NDCG@5', 'NDCG@10'])

display(HTML(nn_tts_results.to_html()))

In [ ]:
from recommenders.amazon_recommender import AmazonRecommender

amazon_recommender = AmazonRecommender()

amazon_tts_results = [['AmazonRecommender'] + list(evaluate_train_test_split_implicit(
    amazon_recommender, interactions_df, items_df))]

amazon_tts_results = pd.DataFrame(
    amazon_tts_results, columns=['Recommender', 'HR@1', 'HR@3', 'HR@5', 'HR@10', 'NDCG@1', 'NDCG@3', 'NDCG@5', 'NDCG@10'])

display(HTML(amazon_tts_results.to_html()))

In [ ]:
from recommenders.netflix_recommender import NetflixRecommender

netflix_recommender = NetflixRecommender(n_epochs=30, print_type='live')

netflix_tts_results = [['NetflixRecommender'] + list(evaluate_train_test_split_implicit(
    netflix_recommender, interactions_df, items_df))]

netflix_tts_results = pd.DataFrame(
    netflix_tts_results, columns=['Recommender', 'HR@1', 'HR@3', 'HR@5', 'HR@10', 'NDCG@1', 'NDCG@3', 'NDCG@5', 'NDCG@10'])

display(HTML(netflix_tts_results.to_html()))

In [ ]:
tts_results = pd.concat([nn_tts_results, amazon_tts_results, netflix_tts_results]).reset_index(drop=True)
display(HTML(tts_results.to_html()))

# Summary

<span style="color:red"><font size="4">**Task:**</font></span><br> 
Write a summary of your experiments. What worked well and what did not? What are your thoughts how could you possibly further improve the model?